In [3]:
!pip install optuna -q

     |████████████████████████████████| 184kB 3.5MB/s eta 0:00:01
     |████████████████████████████████| 1.1MB 8.5MB/s eta 0:00:01
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 81kB 7.6MB/s  eta 0:00:01
     |████████████████████████████████| 81kB 7.4MB/s  eta 0:00:01
     |████████████████████████████████| 61kB 6.5MB/s  eta 0:00:01
     |████████████████████████████████| 112kB 19.0MB/s eta 0:00:01
     |████████████████████████████████| 51kB 5.7MB/s  eta 0:00:01


In [4]:
import pandas as pd
import numpy as np
import random
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import scale
from sklearn.metrics import accuracy_score

import optuna

In [5]:
X_test_mat100 = pd.read_csv('../data/Xte_mat100.csv',sep=' ',header=None).values
X_train_mat100 = pd.read_csv('../data/Xtr_mat100.csv',sep=' ',header=None).values


# X_test = pd.read_csv('../data/Xte.csv',sep=',',index_col=0).values
# X_train = pd.read_csv('../data/Xtr.csv',sep=',',index_col=0).values

y = pd.read_csv('../data/Ytr.csv',sep=',',index_col=0).values

In [6]:
print('x_train: {} y_train {}'.format(X_train_mat100.shape,y.shape))
# print('x_train: {} y_train {}'.format(X_train.shape,y.shape))
# print('x_test: {}'.format(X_test.shape))

x_train: (2000, 100) y_train (2000, 1)


In [7]:
X_train_mat100 = scale(X_train_mat100)

X_train, X_val, y_train, y_val = train_test_split(
    X_train_mat100, y, test_size=0.1, random_state=42)

print(X_train.shape,X_val.shape,y_train.shape, y_val.shape)

(1800, 100) (200, 100) (1800, 1) (200, 1)


### Model Test

In [8]:
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
import seaborn as sns
sns.set()

from sklearn.svm import SVC
from cvxopt import matrix as cvxopt_matrix
from cvxopt import solvers as cvxopt_solvers

In [11]:
C = 10
m,n = X_train.shape
y_train = y_train.reshape(-1,1) * 1.
X_dash = y_train * X_train
H = np.dot(X_dash , X_dash.T) * 1.

#Converting into cvxopt format - as previously
P = cvxopt_matrix(H)
q = cvxopt_matrix(-np.ones((m, 1)))
G = cvxopt_matrix(np.vstack((np.eye(m)*-1,np.eye(m))))
h = cvxopt_matrix(np.hstack((np.zeros(m), np.ones(m) * C)))
A = cvxopt_matrix(y_train.reshape(1, -1))
b = cvxopt_matrix(np.zeros(1))

#Run solver
sol = cvxopt_solvers.qp(P, q, G, h, A, b)
alphas = np.array(sol['x'])

#==================Computing and printing parameters===============================#
w = ((y_train * alphas).T @ X_train).reshape(-1,1)
S = (alphas > 1e-4).flatten()
b = y_train[S] - np.dot(X_train[S], w)

# #Display results
# print('Alphas = ',alphas[alphas > 1e-4])
# print('w = ', w.flatten())
# print('b = ', b[0])

     pcost       dcost       gap    pres   dres
 0: -4.9610e+03 -6.7610e+04  8e+04  1e-01  8e-15
 1: -5.5299e+03 -1.0045e+04  5e+03  7e-03  2e-15
 2: -8.9863e+03 -9.3301e+03  4e+02  3e-04  2e-15
 3: -9.0196e+03 -9.0231e+03  4e+00  3e-06  1e-15
 4: -9.0200e+03 -9.0200e+03  4e-02  3e-08  2e-15
 5: -9.0200e+03 -9.0200e+03  4e-04  3e-10  2e-15
Optimal solution found.


In [12]:
def decision_function(data,w,b):
    return (np.dot(data, w) + b) / np.linalg.norm(w)

In [13]:
#  X_val,y_val
for i in X_val:
    print(decision_function(i,w,b))

[[ 2.07958716e+00]
 [-3.09159859e+00]
 [ 4.33070546e-01]
 [-1.27831495e+00]
 [-8.45476525e-01]
 [-1.05719410e+00]
 [ 3.03630878e+00]
 [-2.78188059e+00]
 [ 3.62126858e-01]
 [-2.98842838e+00]
 [ 2.41433693e-01]
 [-2.13412857e+00]
 [-6.82062688e-01]
 [-2.32208186e+00]
 [ 2.39430048e+00]
 [-2.20278446e+00]
 [-3.60790046e+00]
 [ 1.16333203e+00]
 [ 6.46502571e+00]
 [-1.50692654e+00]
 [-1.86907809e-01]
 [-8.84496681e-01]
 [-1.08628895e+00]
 [-2.16870423e+00]
 [ 1.02319160e-01]
 [-3.76473473e-03]
 [ 4.18638243e+00]
 [ 3.73457580e+00]
 [-3.51516115e+00]
 [-1.15188814e+00]
 [-1.24460462e+00]
 [-1.79114850e+00]
 [ 4.22671810e+00]
 [-3.73757221e+00]
 [-3.88730281e-01]
 [-1.03201332e+00]
 [-1.72695290e+00]
 [-2.52992591e+00]
 [ 1.88515401e+00]
 [-4.27627515e+00]
 [-1.86582373e+00]
 [-1.03464984e+00]
 [-5.53484975e-01]
 [-3.85791314e+00]
 [-2.06193781e+00]
 [-9.72600725e-01]
 [-2.52307403e+00]
 [ 1.76709200e+00]
 [-2.29511911e+00]
 [ 5.97738921e-01]
 [ 4.56944066e-01]
 [-2.82395521e+00]
 [-1.0191344

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

